In [2]:
from pymongo import MongoClient
import numpy as np
import pandas as pd

#Connecting to the Mongo Local server:

client = MongoClient("mongodb://localhost:27017")

#Connecting to my database:

db = client["Olympics"]


In [3]:
#Loading the datasets using pandas

#Store the csv data for each dataset

athletes_data = list(db["Athletes"].find())   
medals_data = list(db["Medals"].find()) 
hosts_data = list(db["Hosts"].find()) 
results_data = list(db["Results"].find()) 

#Converting each one to dataframe to clean it later

athletes_df = pd.DataFrame (athletes_data) 
medals_df = pd.DataFrame(medals_data) 
hosts_df = pd.DataFrame(hosts_data) 
results_df = pd.DataFrame(results_data) 


In [5]:
#Cleaning the athletes dataset

print(athletes_df.head())  #Checking to verify columns that need to be droped.

athletes_df = athletes_df.drop(columns = ["athlete_url" , "bio"])  #dropping athlete_url and bio columns. 

print(athletes_df.head())  #verifying columns dropped

#Making athlete full name lowercase and removing spaces.
athletes_df["athlete_full_name"] = athletes_df["athlete_full_name"].str.lower().str.strip()

print(athletes_df.head())  #verifying columns dropped

#Since there are many null values, I chose to replace them with 0.

#Converting columns to numeric, setting errors='coerce' to replace non-numeric values with NaN
athletes_df["athlete_year_birth"] = pd.to_numeric(athletes_df["athlete_year_birth"], errors='coerce')
athletes_df["games_participations"] = pd.to_numeric(athletes_df["games_participations"], errors='coerce')
athletes_df["athlete_medals"] = pd.to_numeric(athletes_df["athlete_medals"], errors='coerce')

#Replacing NaN values with 0
athletes_df["athlete_year_birth"] = athletes_df["athlete_year_birth"].fillna(0).astype(int)
athletes_df["games_participations"] = athletes_df["games_participations"].fillna(0).astype(int)
athletes_df["athlete_medals"] = athletes_df["athlete_medals"].fillna(0).astype(int)

print(athletes_df.head())  #Cheking to verify the changes

print(medals_df.isnull().sum()) #checking if any column has nulls. 


                        _id athlete_full_name  first_game  athlete_year_birth  \
0  678cb3b27bf16f489ee45be7       dongqi chen  Tokyo 2020                1988   
1  678cb3b27bf16f489ee45be8   sagen maddalena  Tokyo 2020                1993   
2  678cb3b27bf16f489ee45be9   maria martynova  Tokyo 2020                1997   
3  678cb3b27bf16f489ee45bea    yulia karimova  Tokyo 2020                1994   
4  678cb3b27bf16f489ee45beb   najmeh khedmati    Rio 2016                1996   

   athlete_medals  games_participations  
0               0                     0  
1               0                     0  
2               0                     0  
3               0                     1  
4               0                     3  


KeyError: "['athlete_url', 'bio'] not found in axis"

In [6]:
#Cleaning the medals dataset

#Removing rows with missing data. 

medals_df = medals_df.dropna(subset=["athlete_full_name", "country_name"])

#Droping some columns athlete_url is not needed and participant_title and country_code have a lot of null values

medals_df = medals_df.drop(columns = ["athlete_url" , "participant_title", "country_code"])  

#Renaming discipline title column to Sport.

medals_df = medals_df.rename(columns = {"discipline_title": "Sport"})

#Standarizing all string fields and making the medal type to uppercase.

medals_df["athlete_full_name"] = medals_df["athlete_full_name"].str.lower().str.strip()
medals_df["country_name"] = medals_df["country_name"].str.lower().str.strip()
medals_df["medal_type"] = medals_df["medal_type"].str.upper()  #Standardize to uppercase


#Normalizing country names

medals_df["country_name"] = medals_df["country_name"].replace({
    "united states of america": "usa",
    "great britain": "uk",
    "republic of korea": "south korea",
    "federal republic of germany": "germany"})

#Droping duplicate rows 
medals_df = medals_df.drop_duplicates()

print(medals_df.head())

print(medals_df.isnull().sum()) #checking if any column has nulls. 

KeyError: "['athlete_url', 'participant_title', 'country_code'] not found in axis"

In [7]:
#Cleaning the Hosts dataset

#Droping some columns that are not necessary. 

hosts_df = hosts_df.drop(columns = ["game_slug" , "game_end_date", "game_start_date", "game_name"]) 

#Standarizing string texts

hosts_df["game_location"] = hosts_df["game_location"].str.lower().str.strip()
hosts_df["game_season"] = hosts_df["game_season"].str.lower().str.strip()

#Renaming some string values. 

hosts_df["game_location"] = hosts_df["game_location"].replace({
    "united states": "usa",
    "great britain": "uk",
    "republic of korea": "south korea",
    "federal republic of germany": "germany"})

print(hosts_df.head()) #Verifying all went smooth.

KeyError: "['game_slug', 'game_end_date', 'game_start_date', 'game_name'] not found in axis"

In [8]:
#Cleaning the Results dataset

print(results_df.isnull().sum()) #Checking if any column has nulls. 

#Droping unecessary columns to proceed cleaning the rest. 

results_df = results_df.drop(columns = ["rank_equal", "athlete_url", "value_unit","value_type", "country_code","rank_position","athletes"])

#Standarizing string texts for clearance and to rename some values. 

results_df["country_name"] = results_df["country_name"].str.lower().str.strip()
results_df["athlete_full_name"] = results_df["athlete_full_name"].str.lower().str.strip()
results_df["event_title"] = results_df["event_title"].str.lower().str.strip()
results_df["participant_type"] = results_df["participant_type"].str.lower().str.strip()
results_df["medal_type"] = results_df["medal_type"].str.upper().str.strip()

#Renaming some string values
results_df["country_name"] = results_df["country_name"].replace({
    "united states of america": "usa",
    "great britain": "uk",
    "republic of korea": "south korea",
    "federal republic of germany": "germany"})

#Renaming the discipline title column to Sport.
results_df = results_df.rename(columns = {"discipline_title": "Sport"})

#Replacing Null values in medal_type column with NONE_INDIVIDUAL_MEDAL

results_df["medal_type"] = results_df["medal_type"].fillna("NONE_INDIVIDUAL_MEDAL").str.upper()

#Replacing athlete_full_name with "TEAM" where participant_type is "gameteam"
results_df.loc[results_df["participant_type"] == "gameteam", "athlete_full_name"] = "team"

print(results_df.head()) #Viewing to make sure everything is fine.


_id                      0
Sport                    0
event_title              0
slug_game                0
participant_type         0
medal_type               0
country_name             0
country_3_letter_code    0
athlete_full_name        0
dtype: int64


KeyError: "['rank_equal', 'athlete_url', 'value_unit', 'value_type', 'country_code', 'rank_position', 'athletes'] not found in axis"

In [9]:
#Time to load the cleaned datasets back to MongoDB

#Inserting cleaned Athletes dataset
db["Athletes"].drop()  #Clearing the existing data in the collection, while also making sure I dont enter the data twice or more.
db["Athletes"].insert_many(athletes_df.to_dict("records")) #Making sure to insert it as many dictionaries that mongoDB accepts

#Inserting cleaned Medals dataset
db["Medals"].drop()
db["Medals"].insert_many(medals_df.to_dict("records"))

#Inserting cleaned Hosts dataset
db["Hosts"].drop()
db["Hosts"].insert_many(hosts_df.to_dict("records"))

#Inserting cleaned Results dataset
db["Results"].drop()
db["Results"].insert_many(results_df.to_dict("records"))





InsertManyResult([ObjectId('678cb4117bf16f489ee5d34a'), ObjectId('678cb4117bf16f489ee5d34b'), ObjectId('678cb4117bf16f489ee5d34c'), ObjectId('678cb4117bf16f489ee5d34d'), ObjectId('678cb4117bf16f489ee5d34e'), ObjectId('678cb4117bf16f489ee5d34f'), ObjectId('678cb4117bf16f489ee5d350'), ObjectId('678cb4117bf16f489ee5d351'), ObjectId('678cb4117bf16f489ee5d352'), ObjectId('678cb4117bf16f489ee5d353'), ObjectId('678cb4117bf16f489ee5d354'), ObjectId('678cb4117bf16f489ee5d355'), ObjectId('678cb4117bf16f489ee5d356'), ObjectId('678cb4117bf16f489ee5d357'), ObjectId('678cb4117bf16f489ee5d358'), ObjectId('678cb4117bf16f489ee5d359'), ObjectId('678cb4117bf16f489ee5d35a'), ObjectId('678cb4117bf16f489ee5d35b'), ObjectId('678cb4117bf16f489ee5d35c'), ObjectId('678cb4117bf16f489ee5d35d'), ObjectId('678cb4117bf16f489ee5d35e'), ObjectId('678cb4117bf16f489ee5d35f'), ObjectId('678cb4117bf16f489ee5d360'), ObjectId('678cb4117bf16f489ee5d361'), ObjectId('678cb4117bf16f489ee5d362'), ObjectId('678cb4117bf16f489ee5d3

In [30]:

#Access the Olympics database and collections
db = client["Olympics"]
medals_collection = db["Medals"]
hosts_collection = db["Hosts"]

#First Olympics (from Hosts collection)
first_olympics = hosts_collection.find({}).sort("game_year", 1).limit(1)
print("First Olympics:")
for doc in first_olympics:
    print(doc)





First Olympics:
{'_id': ObjectId('678cb3e17bf16f489ee5d348'), 'game_location': 'greece', 'game_season': 'summer', 'game_year': 1896}


In [31]:
#Total Individual Gold Medals for South Korea in Archery
south_korea_gold_archery = list(medals_collection.find({
    "Sport": "Archery", 
    "country_3_letter_code": "KOR", 
    "medal_type": "GOLD"
}))
print("\nSouth Korea Individual Gold Medals in Archery:")
print(f"Count: {len(south_korea_gold_archery)}")
for doc in south_korea_gold_archery:
    print(doc)


South Korea Gold Medals in Archery:
Count: 11
{'_id': ObjectId('678cb3cf7bf16f489ee5826d'), 'Sport': 'Archery', 'slug_game': 'tokyo-2020', 'event_title': "Women's Individual", 'event_gender': 'Women', 'medal_type': 'GOLD', 'participant_type': 'Athlete', 'athlete_full_name': 'san an', 'country_name': 'south korea', 'country_3_letter_code': 'KOR'}
{'_id': ObjectId('678cb3cf7bf16f489ee5878e'), 'Sport': 'Archery', 'slug_game': 'rio-2016', 'event_title': 'Individual competition men', 'event_gender': 'Men', 'medal_type': 'GOLD', 'participant_type': 'Athlete', 'athlete_full_name': 'bonchan ku', 'country_name': 'south korea', 'country_3_letter_code': 'KOR'}
{'_id': ObjectId('678cb3cf7bf16f489ee58791'), 'Sport': 'Archery', 'slug_game': 'rio-2016', 'event_title': 'Individual Competition women', 'event_gender': 'Women', 'medal_type': 'GOLD', 'participant_type': 'Athlete', 'athlete_full_name': 'hyejin chang', 'country_name': 'south korea', 'country_3_letter_code': 'KOR'}
{'_id': ObjectId('678cb3c

In [34]:
#Total Individual Medals for South Korea in Archery
south_korea_archery = list(medals_collection.find({
    "Sport": "Archery", 
    "country_3_letter_code": "KOR"
    }))
print("\nTotal Individual Medals for South Korea in Archery:")
print(f"Count: {len(south_korea_archery)}")


Total Individual Medals for South Korea in Archery:
Count: 25


In [35]:
#South Korea's Performance by Year
south_korea_yearly_performance = medals_collection.aggregate([
    { "$match": { "Sport": "Archery", "country_3_letter_code": "KOR" }},
    { "$group": { "_id": "$slug_game", "total_medals": { "$sum": 1 } }},
    { "$sort": { "_id": 1 }}
])
print("\nSouth Korea's Performance by Year:")
for doc in south_korea_yearly_performance:
    print(doc)


South Korea's Performance by Year:
{'_id': 'athens-2004', 'total_medals': 2}
{'_id': 'atlanta-1996', 'total_medals': 2}
{'_id': 'barcelona-1992', 'total_medals': 3}
{'_id': 'beijing-2008', 'total_medals': 3}
{'_id': 'london-2012', 'total_medals': 2}
{'_id': 'los-angeles-1984', 'total_medals': 2}
{'_id': 'rio-2016', 'total_medals': 3}
{'_id': 'seoul-1988', 'total_medals': 4}
{'_id': 'sydney-2000', 'total_medals': 3}
{'_id': 'tokyo-2020', 'total_medals': 1}


In [40]:
#The athlete who started korean's dominance in archery (hyang-soon seo)
hyang_soon_seo = list(medals_collection.find({
    "Sport": "Archery", 
    "country_3_letter_code": "KOR", 
    "athlete_full_name": "hyang-soon seo"
}))
print("\nAchievements of hyang-soon seo:")
for doc in hyang_soon_seo:
    print(doc)


Achievements of hyang-soon seo:
{'_id': ObjectId('678cb3cf7bf16f489ee5ae35'), 'Sport': 'Archery', 'slug_game': 'los-angeles-1984', 'event_title': 'individual FITA round women', 'event_gender': 'Women', 'medal_type': 'GOLD', 'participant_type': 'Athlete', 'athlete_full_name': 'hyang-soon seo', 'country_name': 'south korea', 'country_3_letter_code': 'KOR'}


In [41]:
#Gender Representation in Archery (South Korea)
gender_representation = medals_collection.aggregate([
    { "$match": { "Sport": "Archery", "country_3_letter_code": "KOR" }},
    { "$group": { "_id": "$event_gender", "total_medals": { "$sum": 1 } }},
    { "$sort": { "total_medals": -1 }}
])
print("\nGender Representation in Archery (South Korea):")
for doc in gender_representation:
    print(doc)


Gender Representation in Archery (South Korea):
{'_id': 'Women', 'total_medals': 19}
{'_id': 'Men', 'total_medals': 6}


In [43]:
#Comparing South Korea to the USA in Archery (Individual matches)
south_korea_total = medals_collection.count_documents({ "Sport": "Archery", "country_3_letter_code": "KOR" })
usa_total = medals_collection.count_documents({ "Sport": "Archery", "country_3_letter_code": "USA" })
print("\nComparison: South Korea vs. USA in Archery:")
print(f"South Korea Individual Total Medals: {south_korea_total}")
print(f"USA Individual Total Medals: {usa_total}")


Comparison: South Korea vs. USA in Archery:
South Korea Individual Total Medals: 25
USA Individual Total Medals: 23
